![NYC Logo](https://www.nyc.gov/assets/tlc/images/content/pages/home/nyc-tlc-logo.svg)

# Convert Parquet Files with NYC Taxi Data to Delta

This notebook uses Spark to read the raw Parquet files of NYC Taxi Data and combine all of the data into one Delta table.

We want to combine all of the individual raw Parquet files into one, master dataset.  However, the schemas for the raw Parquet files vary
between taxi types and change over time within the taxi type. Therefore, we must devote some effort to standardizing the schemas to
one, common schema.

First, specify the location of the raw Parquet files (the input for this process) and the location where we will store the Delta output.

In [0]:
raw_path = "/mnt/taxi/parquet-raw"
delta_path = "/mnt/taxi/delta"

Next, we create a Delta table with the schema we ultimately want for our dataset.  This schema was designed by analyzing the available columns in all of the raw parquet files and determining all of the possible data points we need to capture.

In [0]:
spark.sql("DROP TABLE IF EXISTS taxi")

sql_statement = '''
  CREATE TABLE taxi (
    taxi_type string NOT NULL,
    year int NOT NULL,
    filename string NOT NULL,
    dispatching_base_num string,
    hvfhs_license_num string,
    vendor_id string,
    vendor_name string,
    request_datetime timestamp,
    on_scene_datetime timestamp,
    pickup_datetime timestamp,
    pickup_location_id string,
    pickup_latitude decimal(9, 5),
    pickup_longitude decimal(9, 5),
    dropoff_datetime timestamp,
    dropoff_location_id string,
    dropoff_latitude decimal(9, 5),
    dropoff_longitude decimal(9, 5),
    passenger_count integer,
    trip_distance decimal(9, 5),
    trip_type string,
    payment_type string,
    rate_code string,
    shared_ride string,
    shared_match string,
    store_and_forward string,
    access_a_ride string,
    wav_request string,
    wav_match string,
    fare_amount decimal(8, 2),
    extra decimal(8, 2),
    mta_tax decimal(8, 2),
    tip_amount decimal(8, 2),
    tolls_amount decimal(8, 2),
    improvement_surcharge decimal(8, 2),
    congestion_surcharge decimal(8, 2),
    airport_fee decimal(8, 2),
    ehail_fee decimal(8, 2),
    total_amount decimal(8, 2),
    driver_pay decimal(8, 2)
  )
  USING DELTA
  PARTITIONED BY (taxi_type, year)
  LOCATION '{}'
'''.format(delta_path)

spark.sql(sql_statement)

Out[2]: DataFrame[]

Here's a little function that will recursively search subdirectories in the DBFS and return all of the files in the directory tree.

In [0]:
def getFiles(path):
  files = dbutils.fs.ls(path)
  output = []
  
  for f in files:
    if f.name.endswith("/"):
      output.extend(getFiles(f.path))
    else:
      output.append(f)
  
  return(output)

Now we do the real work!

1. Recursively get all of the raw Parquet files from the input location
2. Loop through all of the files and read each file in as a Spark dataframe.  Don't apply any schema; just read whatever columns we find as strings
3. We add new columns to each dataframe containing the taxi type and the name of the Parquet file from which the data was read
4. Some of the Parquet files may have leading spaces in the column names(?)  We rename those columns to remove those spaces and to convert all column names to lowercase (for consistency)
5. The names of the columns can vary between files.  So we've hard-coded a mapping to convert column names to a standard name.
6. For any columns with a name ending in "datetime", parse the string contents of the column into a timestamp
7. Add a new column by extracting the year from the `pickup_datetime` column
8. Compare the schema of our dataframe to the target Delta table.  If there are any columns missing from our dataframe, add them with `null` values.
9. Loop through all of the columns in our dataframe.  If a column's datatype doesn't match the datatype in the target Delta table, cast the column to the appropriate datatype.
10. Reorder the columns in our dataframe to match the order of columns in the target Delta table.
11. At last!  We insert the dataframe into the Delta table.  This writes the data out as Parquet in our target location.
12. Go back to Step 2 and process the next raw Parquet file.

In [0]:
import pyspark.sql.functions as pyf
from pyspark.sql import Row

all_files = getFiles(raw_path)

target_cols = sqlContext.table("taxi").dtypes

# Loop through all of the raw files
for f in all_files:
  print("Processing file {}".format(f))
  
  taxi_type = f.path.split('/')[-2]
  
  # Use Spark to read the current parquet file into a dataframe and add some new columns
  raw_df = spark\
            .read\
            .parquet(f.path)\
            .withColumn("filename",  pyf.input_file_name())\
            .withColumn("taxi_type", pyf.lit(taxi_type))
  
  # Remove spaces from column names and convert to lowercase
  for n in raw_df.schema.names:
    clean_name = n.strip().lower()
    if n != clean_name:
      raw_df = raw_df.withColumnRenamed(n, clean_name)
  
  # Convert columns to standard names
  if "dolocationid"          in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("dolocationid", "dropoff_location_id")
  if "end_lat"               in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("end_lat", "dropoff_latitude")
  if "end_lon"               in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("end_lon", "dropoff_longitude")
  if "fare_amt"              in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("fare_amt", "fare_amount")
  if "improvement_surcharge" in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("improvement_surcharge", "surcharge")
  if "locationid"            in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("locationid", "pickup_location_id")
  if "lpep_dropoff_datetime" in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("lpep_dropoff_datetime", "dropoff_datetime")
  if "lpep_pickup_datetime"  in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("lpep_pickup_datetime", "pickup_datetime")
  if "pickup_date"           in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("pickup_date", "pickup_datetime")
  if "pulocationid"          in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("pulocationid", "pickup_location_id")
  if "ratecodeid"            in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("ratecodeid", "rate_code")
  if "sr_flag"               in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("sr_flag", "shared_ride")
  if "start_lat"             in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("start_lat", "pickup_latitude")
  if "start_lon"             in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("start_lon", "pickup_longitude")
  if "store_and_fwd_flag"    in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("store_and_fwd_flag", "store_and_forward")
  if "surcharge"             in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("surcharge", "improvement_surcharge")
  if "tip_amt"               in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("tip_amt", "tip_amount")
  if "tolls_amt"             in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("tolls_amt", "tolls_amount")
  if "total_amt"             in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("total_amt", "total_amount")
  if "tpep_dropoff_datetime" in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("tpep_dropoff_datetime", "dropoff_datetime")
  if "tpep_pickup_datetime"  in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("tpep_pickup_datetime", "pickup_datetime")
  if "trip_dropoff_datetime" in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("trip_dropoff_datetime", "dropoff_datetime")
  if "trip_pickup_datetime"  in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("trip_pickup_datetime", "pickup_datetime")
  if "vendorid"              in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("vendorid", "vendor_id")
  if "trip_miles"            in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("trip_miles", "trip_distance")
  if "base_passenger_fare"   in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("base_passenger_fare", "fare_amount")
  if "tolls"                 in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("tolls", "tolls_amount")
  if "sales_tax"             in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("sales_tax", "mta_tax")
  if "tips"                  in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("tips", "tip_amount")
  if "shared_request_flag"   in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("shared_request_flag", "shared_ride")
  if "shared_match_flag"     in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("shared_match_flag", "shared_match")
  if "access_a_ride_flag"    in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("access_a_ride_flag", "access_a_ride")
  if "wav_request_flag"      in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("wav_request_flag", "wav_request")
  if "wav_match_flag"        in raw_df.schema.names: raw_df = raw_df.withColumnRenamed("wav_match_flag", "wav_match")


  # Parse datetime columns to a timestamp
  for dt in raw_df.dtypes:
    if dt[0].endswith("datetime") and dt[1] == "string":
      raw_df = raw_df.withColumn(dt[0], pyf.to_timestamp(dt[0], 'yyyy-MM-dd HH:mm:ss'))
  
  # Add a "year" column
  raw_df = raw_df.withColumn("year", pyf.year("pickup_datetime"))

  # Print a note about any columns in the raw df that don't match the output
  for dt in raw_df.dtypes:
    if dt[0] not in [i[0] for i in target_cols]:
      print(f"   No mapping for column \"{dt[0]}\". It will be skipped.")

  # Add missing columns
  for tc in target_cols:
    if tc[0] not in raw_df.schema.names:
      raw_df = raw_df.withColumn(tc[0], pyf.lit(None))

  # Make columns datatype match target
  for tc in target_cols:
    ac = next(x for x in raw_df.dtypes if x[0] == tc[0])
    if ac[1] != tc[1]:
      raw_df = raw_df.withColumn(ac[0], raw_df[ac[0]].cast(tc[1]))

  # Reorder columns to match target
  raw_df = raw_df.select([x[0] for x in target_cols])

  raw_df.write.insertInto("taxi", overwrite = False)

Processing file FileInfo(path='dbfs:/mnt/taxi/parquet-raw/fhv/2015-01.parquet', name='2015-01.parquet', size=12111775, modificationTime=1663962251000)
   No mapping for column "affiliated_base_number". It will be skipped.
Processing file FileInfo(path='dbfs:/mnt/taxi/parquet-raw/fhv/2015-02.parquet', name='2015-02.parquet', size=13671243, modificationTime=1663962253000)
   No mapping for column "affiliated_base_number". It will be skipped.
Processing file FileInfo(path='dbfs:/mnt/taxi/parquet-raw/fhv/2015-03.parquet', name='2015-03.parquet', size=9047823, modificationTime=1663962254000)
   No mapping for column "affiliated_base_number". It will be skipped.
Processing file FileInfo(path='dbfs:/mnt/taxi/parquet-raw/fhv/2015-04.parquet', name='2015-04.parquet', size=10762303, modificationTime=1663962255000)
   No mapping for column "affiliated_base_number". It will be skipped.
Processing file FileInfo(path='dbfs:/mnt/taxi/parquet-raw/fhv/2015-05.parquet', name='2015-05.parquet', size=1200

Because we loaded the raw Parquet data into our table with multiple writes, we will have many small files in our Delta table.
Use Databricks Delta functionality to clean up those files and optimize the file layout.

In [0]:
spark.sql("OPTIMIZE taxi ZORDER BY (pickup_datetime)")

spark.conf.set("spark.databricks.delta.retentionDurationCheck.enabled", 'false')
spark.sql("VACUUM taxi RETAIN 0 hours")
spark.conf.set("spark.databricks.delta.retentionDurationCheck.enabled", 'true')

We're all done!  Now we just need to check our work to make sure everything looks good.

First, read all of the raw Parquet files at once and count the rows in them.  Compare that count to the Delta table to make sure we have the same number of rows.

In [0]:
full_raw_df = spark.read.parquet(f"{raw_path}/*/*.parquet")
delta_df = spark.read.format("delta").load(delta_path)

print(f"Raw Parquet Count: {full_raw_df.count():,}")
print(f"      Delta Count: {delta_df.count():,}")

Raw Parquet Count: 3,326,737,830
      Delta Count: 3,326,737,830


Now create a nice matrix that shows the number of rows by `year` and `taxi_type`.  Add a column that shows the total rows
for each year and a summary row at the bottom that shows the number of rows for each taxi type.

In [0]:
import pyspark.sql.functions as pyf

delta_df = spark.read.format("delta").load(delta_path)

# Summarize the row counts by year and taxi_type
summary_df = delta_df\
              .withColumn("year", pyf.col("year").cast("string"))\
              .groupBy("year")\
              .pivot("taxi_type")\
              .count()\
              .fillna(0)\
              .orderBy("year")

# Add a "total" column that shows the total counts for each year
summary_df = summary_df.withColumn('total', sum(summary_df[col] for col in summary_df.columns if col != "year"))

# Add a summary row that shows the total counts for each column
exprs = [pyf.sum(x).alias(x) for x in summary_df.columns if x != "year"]
summary_row = summary_df.agg(*exprs).selectExpr("'total' AS year", "*")
summary_df = summary_df.union(summary_row)

display(summary_df)

year fhv fhvhv green yellow total 2001 0 0 0 21 21 2002 0 0 0 476 476 2003 0 0 0 44 44 2004 0 0 0 1 1 2008 0 0 109 743 852 2009 0 0 310 170897321 170897631 2010 0 0 348 169001154 169001502 2011 0 0 0 176887272 176887272 2012 0 0 3 171359008 171359011 2013 0 0 0 171816340 171816340 2014 0 0 15837009 165447579 181284588 2015 63388532 0 19233765 146039232 228661529 2016 132114083 0 16385541 131131805 279631429 2017 192309557 0 11736906 113500386 317546849 2018 260874754 0 8899314 102870524 372644592 2019 43261276 234630264 6300814 84597309 368789663 2020 14945465 143309871 1734166 24649266 184638768 2021 14805265 174596652 1068729 30903983 221374629 2022 14511664 212416083 840394 39655622 267423763 2023 2225117 36440002 133016 5980684 44778819 2026 0 0 0 3 3 2028 0 0 0 1 1 2029 0 0 0 7 7 2030 0 0 2 0 2 2031 0 0 0 2 2 2032 0 0 0 1 1 2033 0 0 0 3 3 2035 0 0 1 0 1 2037 0 0 0 1 1 2038 0 0 0 4 4 2041 0 0 1 3 4 2042 0 0 0 1 1 2053 0 0 0 2 2 2058 0 0 0 3 3 2062 0 0 1 0 1 2066 0 0 0 1 1 2070 0 0 0 1 1 2081 0 0 1 0 1 2084 0 0 0 8 8 2088 0 0 0 2 2 2090 0 0 0 1 1 2098 0 0 0 1 1 total 738435713 801392872 82170430 1704738815 3326737830

Just for fun, add a visualization that shows the rowcounts by year.  This lets us see that yellow taxi rides are declining over time while FHV rides are exploding.

In [0]:
display(
  delta_df\
    .filter("year BETWEEN 2009 AND 2023")\
    .groupBy("year")\
    .pivot("taxi_type")\
    .count()\
    .orderBy("year")
)

year fhv fhvhv green yellow 2009 null null 310 170897321 2010 null null 348 169001154 2011 null null null 176887272 2012 null null 3 171359008 2013 null null null 171816340 2014 null null 15837009 165447579 2015 63388532 null 19233765 146039232 2016 132114083 null 16385541 131131805 2017 192309557 null 11736906 113500386 2018 260874754 null 8899314 102870524 2019 43261276 234630264 6300814 84597309 2020 14945465 143309871 1734166 24649266 2021 14805265 174596652 1068729 30903983 2022 14511664 212416083 840394 39655622 2023 2225117 36440002 133016 5980684

Databricks data profile. Run in Databricks to view.